In [1]:
import os
import torch
import torch.nn as nn
import pdb
import logging

from tqdm import tqdm
from sklearn.metrics import precision_recall_fscore_support
from dataset import CustomDataLoader
from torch.utils.data import DataLoader
from model import ERC_model
from transformers import RobertaModel
from transformers import get_linear_schedule_with_warmup

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [3]:
dev_dataset = CustomDataLoader('./MELD/data/MELD/dev_sent_emo.csv')
dev_dataloader = DataLoader(dev_dataset, batch_size=3, shuffle=False, num_workers=4, collate_fn=dev_dataset.collate_fn)

for i, data in enumerate(dev_dataloader):
    if i == 1:
        print(data[0].shape)
        batch_padding_token, batch_padding_attention_mask, batch_PM_input, batch_label = data
        print("batch_padding_token", batch_padding_token)
        print("batch_padding_attention_mask", batch_padding_attention_mask)
        print("batch_PM_input", batch_PM_input)
        print("batch_label", batch_label)
        break

torch.Size([3, 58])
batch_padding_token tensor([[    0,  1793,   328,  1793,     6,    52,   115,   213,     7,     5,
           827,     6,   593,    84,  2349,     8,   847,   106,   160,    23,
             5,  1300,     4,     2,   370,    17,    27,   241,    10, 16333,
           328,     2,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1],
        [    0,  1793,   328,  1793,     6,    52,   115,   213,     7,     5,
           827,     6,   593,    84,  2349,     8,   847,   106,   160,    23,
             5,  1300,     4,     2,   370,    17,    27,   241,    10, 16333,
           328,     2,    83, 33130,     6,   313,     6,   122,    52,   351,
            17,    27,    90,    28,   827, 30489,   328,     2,     1,     1,
             1,     1,     1,     1,     1,     1,     1,     1],
        [    0,  1793,   328,  1793,  

In [4]:
train_dataset = CustomDataLoader('./MELD/data/MELD/train_sent_emo.csv')
dev_dataset = CustomDataLoader('./MELD/data/MELD/dev_sent_emo.csv')
test_dataset = CustomDataLoader('./MELD/data/MELD/test_sent_emo.csv')

train_dataloader = DataLoader(train_dataset, batch_size=1, shuffle=True, num_workers=4, collate_fn=train_dataset.collate_fn)
dev_dataloader = DataLoader(dev_dataset, batch_size=1, shuffle=False, num_workers=4, collate_fn=dev_dataset.collate_fn)
test_dataloader = DataLoader(test_dataset, batch_size=1, shuffle=False, num_workers=4, collate_fn=test_dataset.collate_fn)

In [5]:
from model import ERC_model
clsNum = len(train_dataset.emoList)
erc_model = ERC_model(clsNum).cuda()

In [6]:
def cal_accuracy(model, dataloader):
    model.eval()
    correct = 0
    label_list = []
    pred_list = []
    
    # label arragne
    with torch.no_grad():
        for i_batch, data in enumerate(tqdm(dataloader)):
            batch_padding_token, batch_padding_attention_mask, batch_PM_input, batch_label = data
            batch_padding_token = batch_padding_token.cuda()
            batch_padding_attention_mask = batch_padding_attention_mask.cuda()
            batch_PM_input = [[x2.cuda() for x2 in x1] for x1 in batch_PM_input]
            batch_label = batch_label.cuda()        

            # Prediction
            pred_logits = erc_model(batch_padding_token, batch_padding_attention_mask, batch_PM_input)
            
            # Calculation
            pred_label = pred_logits.argmax(1).item()
            true_label = batch_label.item()
            
            pred_list.append(pred_label)
            label_list.append(true_label)
            if pred_label == true_label:
                correct += 1
        acc = correct/len(dataloader)
    return acc, pred_list, label_list

In [7]:
dev_acc, dev_pred_list, dev_label_list = cal_accuracy(erc_model, dev_dataloader)
dev_pre, dev_rec, dev_fbeta, _ = precision_recall_fscore_support(dev_label_list, dev_pred_list, average='weighted')

100%|████████████████████████████████████████████████████| 1109/1109 [00:13<00:00, 84.47it/s]
/home/userpc-01/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [8]:
def cross_entropy_loss(pred_outs, labels):
    loss = nn.CrossEntropyLoss()
    loss_val = loss(pred_outs, labels)
    return loss_val

In [11]:
CFG = {
    'EPOCHS': 5,
    'MAX_GRAD_NORM': 10,
    'LEARNING_RATE': 1e-6
}

In [15]:
num_training_steps = len(train_dataset)*CFG['EPOCHS']
num_warmup_steps = len(train_dataset)
optimizer = torch.optim.AdamW(erc_model.parameters(), lr=CFG['LEARNING_RATE'])
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=num_warmup_steps, num_training_steps=num_training_steps)

for epoch in tqdm(range(CFG['EPOCHS'])):
    erc_model.train() 
    for i_batch, data in enumerate(train_dataloader):
        batch_padding_token, batch_padding_attention_mask, batch_PM_input, batch_label = data
        batch_padding_token = batch_padding_token.cuda()
        batch_padding_attention_mask = batch_padding_attention_mask.cuda()
        batch_PM_input = [[x2.cuda() for x2 in x1] for x1 in batch_PM_input]
        batch_label = batch_label.cuda()        
        
        pred_logits = erc_model(batch_padding_token, batch_padding_attention_mask, batch_PM_input)
        
        loss_val = cross_entropy_loss(pred_logits, batch_label)
        
        loss_val.backward()
        torch.nn.utils.clip_grad_norm_(erc_model.parameters(), CFG['MAX_GRAD_NORM'])
        optimizer.step()
        scheduler.step()
        optimizer.zero_grad()        
        break
    break

  0%|                                                                  | 0/5 [00:00<?, ?it/s]


In [18]:
def SaveModel(model, path):
    if not os.path.exists(path):
        os.makedirs(path)
    torch.save(model.state_dict(), os.path.join(path, 'model.bin'))

In [19]:
import math
a = -(0.8*math.log(0.8)+0.2*math.log(0.2))
b = -(0.8*math.log(0.5)+0.2*math.log(0.5))
a, b

(0.5004024235381879, 0.6931471805599453)

In [23]:
# 로그 생성
logger = logging.getLogger()

# 로그의 출력 기준 설정
logger.setLevel(logging.INFO)

# log 출력
stream_handler = logging.StreamHandler()
logger.addHandler(stream_handler)

# log를 파일에 출력
file_handler = logging.FileHandler('erc.log')
logger.addHandler(file_handler)


best_dev_fscore = 0
save_path = '.'
for epoch in tqdm(range(CFG['EPOCHS'])):
    erc_model.train() 
    for i_batch, data in enumerate(tqdm(train_dataloader)):
        batch_padding_token, batch_padding_attention_mask, batch_PM_input, batch_label = data
        batch_padding_token = batch_padding_token.cuda()
        batch_padding_attention_mask = batch_padding_attention_mask.cuda()
        batch_PM_input = [[x2.cuda() for x2 in x1] for x1 in batch_PM_input]
        batch_label = batch_label.cuda()        
        
        pred_logits = erc_model(batch_padding_token, batch_padding_attention_mask, batch_PM_input)
        
        loss_val = cross_entropy_loss(pred_logits, batch_label)
        
        loss_val.backward()
        torch.nn.utils.clip_grad_norm_(erc_model.parameters(), CFG['MAX_GRAD_NORM'])
        optimizer.step()
        scheduler.step()
        optimizer.zero_grad()
    
    erc_model.eval()
    
    dev_acc, dev_pred_list, dev_label_list = cal_accuracy(erc_model, dev_dataloader)
    dev_pre, dev_rec, dev_fbeta, _ = precision_recall_fscore_support(dev_label_list, dev_pred_list, average='weighted')
    
    logger.info("Dev W-avg F1: {}".format(dev_fbeta))
    
    test_acc, test_pred_list, test_label_list = cal_accuracy(erc_model, test_dataloader)
    
    # if model is best score,
    if dev_fbeta > best_dev_fscore:
        best_dev_fscore = dev_fbeta

        test_acc, test_pred_list, test_label_list = cal_accuracy(erc_model, test_dataloader)
        test_pre, test_rec, test_fbeta, _ = precision_recall_fscore_support(test_label_list, test_pred_list, average='weighted')                

        SaveModel(erc_model, save_path)
        logger.info("Epoch:{}, Test W-avg F1: {}".format(epoch, test_fbeta))

  1%|▌                                                                                                | 56/9989 [00:07<22:19,  7.42it/s]


  1%|█                                                                                               | 114/9989 [00:17<24:11,  6.80it/s]


  2%|█▋                                                                                              | 172/9989 [00:25<25:14,  6.48it/s]


  2%|██▏                                                                                             | 230/9989 [00:33<22:24,  7.26it/s]


  3%|██▊                                                                                             | 288/9989 [00:41<18:56,  8.54it/s]


...

100%|███████████████████████████████████████████████████████████████████████████████████████████████| 1109/1109 [00:13<00:00, 82.76it/s]
Dev W-avg F1: 0.5752329106594903

  6%|█████▊                                                                                          | 158/2610 [00:01<00:25, 97.94it/s]Token indices sequence length is longer than the specified maximum sequence length for this model (522 > 512). Running this sequence through the model will result in indexing errors

  6%|██████▏                                                                                         | 169/2610 [00:01<00:29, 81.94it/s]Token indices sequence length is longer than the specified maximum sequence length for this model (547 > 512). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (560 > 512). Running this sequence through the model will result in indexing errors
Token indi

 34%|████████████████████████████████▉                                                               | 897/2610 [00:10<00:25, 67.46it/s]


 58%|██████████████████████████████████████████████████████▋                                        | 1504/2610 [00:18<00:13, 82.50it/s]


 82%|█████████████████████████████████████████████████████████████████████████████▋                 | 2134/2610 [00:26<00:05, 80.39it/s]


100%|█████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [2:06:17<00:00, 1515.47s/it]


In [24]:
best_dev_fscore

0.5752329106594903

In [25]:
!touch train.py

In [29]:
!python3 train.py

In [30]:
def error_case(model, dataloader):
    model.eval()
    correct = 0
    label_list = []
    pred_list = []    
    
    error_samples = []
    # label arragne
    with torch.no_grad():
        for i_batch, data in enumerate(tqdm(dataloader)):
            """Prediction"""
            batch_padding_token, batch_padding_attention_mask, batch_PM_input, batch_label = data
            batch_padding_token = batch_padding_token.cuda()
            batch_padding_attention_mask = batch_padding_attention_mask.cuda()
            batch_PM_input = [[x2.cuda() for x2 in x1] for x1 in batch_PM_input]
            batch_label = batch_label.cuda()        

            """Prediction"""
            pred_logits = erc_model(batch_padding_token, batch_padding_attention_mask, batch_PM_input)
            
            """Calculation"""    
            pred_label = pred_logits.argmax(1).item()
            true_label = batch_label.item()
            
            pred_list.append(pred_label)
            label_list.append(true_label)            
            if pred_label != true_label:
                error_samples.append([batch_padding_token, true_label, pred_label])
            if pred_label == true_label:
                correct += 1
        acc = correct/len(dataloader)                
    return error_samples, acc, pred_list, label_list

In [31]:
error_samples, acc, pred_list, label_list = error_case(erc_model, test_dataloader)

  6%|██████▏                                                                                         | 169/2610 [00:01<00:30, 81.08it/s]Token indices sequence length is longer than the specified maximum sequence length for this model (547 > 512). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (560 > 512). Running this sequence through the model will result in indexing errors
Token indices sequence length is longer than the specified maximum sequence length for this model (597 > 512). Running this sequence through the model will result in indexing errors
100%|███████████████████████████████████████████████████████████████████████████████████████████████| 2610/2610 [00:32<00:00, 80.84it/s]


In [33]:
import random
random_error_samples = random.sample(error_samples, 5)

In [34]:
for random_error_sample in random_error_samples:
    batch_padding_token, true_label, pred_label = random_error_sample
    print('--------------------------------------------------------')
    print("Input Sentence: ", test_dataset.tokenizer.decode(batch_padding_token.squeeze(0).tolist()))
    print("Actual Emotion: ", test_dataset.emoList[true_label])
    print("Predictive Emotion: ", test_dataset.emoList[pred_label])

--------------------------------------------------------
Input Sentence:  <s> Well, alright, we already tried feeding her, changing her,  burping her, oh try this one!</s> Go back in time and listen to Phoebe!</s>
Actual Emotion:  anger
Predictive Emotion:  joy
--------------------------------------------------------
Input Sentence:  <s> Did he call?</s> No. Sorry.</s> Why?! Why?! He said he’d call. Why hasn’t he called?</s>
Actual Emotion:  sadness
Predictive Emotion:  surprise
--------------------------------------------------------
Input Sentence:  <s> Y’know I don’t understand why they didn’t cry. It was a beautiful speech.</s> Oh, come on.</s> Hey!</s>
Actual Emotion:  sadness
Predictive Emotion:  joy
--------------------------------------------------------
Input Sentence:  <s> Hey. When you guys were kids and you played</s> I was always Joanne.</s> Question. Was ah, ‘Egg the Gellers!’ the war cry of your neighbourhood?</s> Ewww! Oh! It’s the Mattress King!</s> Don’t look honey. C